In [6]:
%%writefile run.py
# Import necessary libraries
import sys
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from xgboost import XGBRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

# Load the training data
train_data = pd.read_csv('train_data.csv')

# Drop columns not needed for training (e.g., uuid, datasetId, condition)
train_data = train_data.drop(['uuid', 'datasetId', 'condition'], axis=1)

# Separate features and target variable
X = train_data.drop('HR', axis=1)
y = train_data['HR']

# Split the data into training and validation sets
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=42)

# Standardize features
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_valid_scaled = scaler.transform(X_valid)

# Train the XGBoost model
model = XGBRegressor()
model.fit(X_train_scaled, y_train)

# Predict on the validation set
y_pred = model.predict(X_valid_scaled)

# Evaluate the model
rmse = np.sqrt(mean_squared_error(y_valid, y_pred))
mae = mean_absolute_error(y_valid, y_pred)
r2 = r2_score(y_valid, y_pred)
#print(f"RMSE: {rmse:.2f}, MAE: {mae:.2f}, R2: {r2:.2f}")

# Save the trained model for later use
model.save_model('heart_rate_model.model')

# Load the test data
test_data = pd.read_csv(sys.argv[1])

# Drop columns not needed for prediction (e.g., datasetId, condition)
test_data = test_data.drop(['datasetId', 'condition'], axis=1)

# Extract the 'uuid' column for later inclusion in the results
uuid_column = test_data['uuid']

# Drop 'uuid' column as it's not needed for prediction
test_data = test_data.drop(['uuid'], axis=1)

# Load the trained model
model = XGBRegressor()
model.load_model('heart_rate_model.model')

# Standardize features
scaler = StandardScaler()

# Exclude non-numeric columns before scaling
numeric_columns = test_data.select_dtypes(include=['float64', 'int64']).columns
test_data[numeric_columns] = scaler.fit_transform(test_data[numeric_columns])

# Predict on the test set
predictions = model.predict(test_data)

# Create a DataFrame with 'uuid' and predicted heart rates
result_df = pd.DataFrame({'uuid': uuid_column, 'Predicted_HR': predictions})

# Save the predictions to results.csv
result_df.to_csv('results.csv', index=False)


Overwriting run.py


In [7]:
!python3 run.py sample_test_data.csv

/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning: [17:39:38] WARNING: /workspace/src/c_api/c_api.cc:1240: Saving into deprecated binary model format, please consider using `json` or `ubj`. Model format will default to JSON in XGBoost 2.2 if not specified.
  warnings.warn(smsg, UserWarning)


In [8]:
!diff sample_output_generated.csv results.csv

1,11c1,11
< uuid,HR
< 1ae30e0b-098e-46fc-a897-0a6661f26370,75.20605018136611
< 428b41b3-9461-4c79-ab4e-d03b122b2553,80.87013184541209
< 88f82ac7-02dd-447e-a289-22e8e22432c2,62.313062562993096
< 1d09b18f-d82f-4c1a-bb2d-71fda6fea837,66.33692439456603
< a6302640-f70a-4a3a-ad36-a8c3d5df9400,64.42259563691518
< 3f6508be-4b0a-4008-b701-49d8c2d5dd43,56.06109451648653
< a07d84c8-fc44-45ef-bb85-f06f06b70e9f,75.54367313179301
< f4a449db-a7ff-437b-852b-821a6e965f2f,62.45828058775175
< 94364ef1-12e2-4ddd-9f35-99e270547849,56.27187553358296
< 231d34f5-1028-4f2e-8e1d-00d086b0c218,71.20150079650375
---
> uuid,Predicted_HR
> 1ae30e0b-098e-46fc-a897-0a6661f26370,84.88413
> 428b41b3-9461-4c79-ab4e-d03b122b2553,90.85277
> 88f82ac7-02dd-447e-a289-22e8e22432c2,68.22056
> 1d09b18f-d82f-4c1a-bb2d-71fda6fea837,74.494804
> a6302640-f70a-4a3a-ad36-a8c3d5df9400,71.14344
> 3f6508be-4b0a-4008-b701-49d8c2d5dd43,59.71483
> a07d84c8-fc44-45ef-bb85-f06f06b70e9f,84.0379
> f4a449db-a7ff-437b-852b-821a6e965f2f,68.14893
>

## Candidate model: LSTM

In [9]:
# Import the libraries
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Conv1D, MaxPooling1D, Flatten
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score

# Load the data
data = pd.read_csv("train_data.csv")

# Split the data into features and target
X = data.drop(["uuid", "datasetId", "condition", "HR"], axis=1) # Features
y = data["HR"] # Target

# Normalize the features
X = (X - X.mean()) / X.std()

# Reshape the features for LSTM or CNN input
X = np.array(X).reshape(X.shape[0], X.shape[1], 1)

# Split the data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# LSTM model
model = Sequential()
model.add(LSTM(64, input_shape=(X.shape[1], X.shape[2])))
model.add(Dense(32, activation="relu"))
model.add(Dense(1))

# Compile the model
model.compile(loss="mse", optimizer=Adam(learning_rate=0.001), metrics=["mae"])

# Train the model
model.fit(X_train, y_train, epochs=10, batch_size=32, validation_split=0.2)

# Evaluate the model on the test set
y_pred = model.predict(X_test)
mse = mean_squared_error(y_test, y_pred)
mae = tf.keras.losses.MeanAbsoluteError()(y_test, y_pred)
r2 = r2_score(y_test, y_pred)
print(f"MSE: {mse:.2f}, MAE: {mae:.2f}, R2: {r2:.2f}")


Epoch 1/10
100/100 [==============================] - 6s 42ms/step - loss: 3532.9766 - mae: 56.9951 - val_loss: 1196.2904 - val_mae: 32.9010
Epoch 2/10
100/100 [==============================] - 3s 32ms/step - loss: 380.2331 - mae: 15.6761 - val_loss: 118.3007 - val_mae: 8.6549
Epoch 3/10
100/100 [==============================] - 3s 29ms/step - loss: 111.1441 - mae: 8.2732 - val_loss: 113.8861 - val_mae: 8.4873
Epoch 4/10
100/100 [==============================] - 2s 17ms/step - loss: 110.8515 - mae: 8.2522 - val_loss: 113.9066 - val_mae: 8.4891
Epoch 5/10
100/100 [==============================] - 2s 17ms/step - loss: 110.8430 - mae: 8.2525 - val_loss: 113.7464 - val_mae: 8.4781
Epoch 6/10
100/100 [==============================] - 2s 25ms/step - loss: 110.8910 - mae: 8.2553 - val_loss: 113.7804 - val_mae: 8.4830
Epoch 7/10
100/100 [==============================] - 2s 16ms/step - loss: 110.8878 - mae: 8.2587 - val_loss: 113.9575 - val_mae: 8.4936
Epoch 8/10
100/100 [================

## Alternate model: CNN

In [10]:
# Import the libraries
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Conv1D, MaxPooling1D, Flatten
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score

# Load the data
data = pd.read_csv("train_data.csv")

# Split the data into features and target
X = data.drop(["uuid", "datasetId", "condition", "HR"], axis=1) # Features
y = data["HR"] # Target

# Normalize the features
X = (X - X.mean()) / X.std()

# Reshape the features for LSTM or CNN input
X = np.array(X).reshape(X.shape[0], X.shape[1], 1)

# Split the data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# CNN model
model = Sequential()
model.add(Conv1D(32, 3, activation="relu", input_shape=(X.shape[1], X.shape[2])))
model.add(MaxPooling1D(2))
model.add(Flatten())
model.add(Dense(32, activation="relu"))
model.add(Dense(1))

# Compile the model
model.compile(loss="mse", optimizer=Adam(learning_rate=0.001), metrics=["mae"])

# Train the model
model.fit(X_train, y_train, epochs=10, batch_size=32, validation_split=0.2)

# Evaluate the model on the test set
y_pred = model.predict(X_test)
mse = mean_squared_error(y_test, y_pred)
mae = tf.keras.losses.MeanAbsoluteError()(y_test, y_pred)
r2 = r2_score(y_test, y_pred)
print(f"MSE: {mse:.2f}, MAE: {mae:.2f}, R2: {r2:.2f}")




Epoch 1/10
100/100 [==============================] - 1s 5ms/step - loss: 2655.2791 - mae: 45.6415 - val_loss: 331.7001 - val_mae: 14.2804
Epoch 2/10
100/100 [==============================] - 0s 3ms/step - loss: 248.7074 - mae: 12.2313 - val_loss: 181.9939 - val_mae: 10.6170
Epoch 3/10
100/100 [==============================] - 0s 4ms/step - loss: 159.2415 - mae: 9.8676 - val_loss: 130.8214 - val_mae: 8.9930
Epoch 4/10
100/100 [==============================] - 0s 3ms/step - loss: 112.3128 - mae: 8.3457 - val_loss: 93.6723 - val_mae: 7.6824
Epoch 5/10
100/100 [==============================] - 0s 4ms/step - loss: 80.4597 - mae: 7.0770 - val_loss: 67.8379 - val_mae: 6.5348
Epoch 6/10
100/100 [==============================] - 0s 4ms/step - loss: 57.9710 - mae: 6.0347 - val_loss: 49.7574 - val_mae: 5.5823
Epoch 7/10
100/100 [==============================] - 0s 4ms/step - loss: 42.5359 - mae: 5.1559 - val_loss: 37.2787 - val_mae: 4.8118
Epoch 8/10
100/100 [==============================

##Final Model: XGBoost

In [11]:
# Import necessary libraries
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from xgboost import XGBRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

# Load the training data
train_data = pd.read_csv('train_data.csv')

# Drop columns not needed for training (e.g., uuid, datasetId, condition)
train_data = train_data.drop(['uuid', 'datasetId', 'condition'], axis=1)

# Separate features and target variable
X = train_data.drop('HR', axis=1)
y = train_data['HR']

# Split the data into training and validation sets
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=42)

# Standardize features
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_valid_scaled = scaler.transform(X_valid)

# Train the XGBoost model
model = XGBRegressor()
model.fit(X_train_scaled, y_train)

# Predict on the validation set
y_pred = model.predict(X_valid_scaled)

# Evaluate the model
rmse = np.sqrt(mean_squared_error(y_valid, y_pred))
mae = mean_absolute_error(y_valid, y_pred)
r2 = r2_score(y_valid, y_pred)
print(f"RMSE: {rmse:.2f}, MAE: {mae:.2f}, R2: {r2:.2f}")

# Save the trained model for later use
model.save_model('heart_rate_model.model')


RMSE: 0.41, MAE: 0.21, R2: 1.00


/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning: [17:40:42] WARNING: /workspace/src/c_api/c_api.cc:1240: Saving into deprecated binary model format, please consider using `json` or `ubj`. Model format will default to JSON in XGBoost 2.2 if not specified.
  warnings.warn(smsg, UserWarning)


In [12]:
# Load the test data
test_data = pd.read_csv('sample_test_data.csv')

# Drop columns not needed for prediction (e.g., datasetId, condition)
test_data = test_data.drop(['datasetId', 'condition'], axis=1)

# Extract the 'uuid' column for later inclusion in the results
uuid_column = test_data['uuid']

# Drop 'uuid' column as it's not needed for prediction
test_data = test_data.drop(['uuid'], axis=1)

# Load the trained model
model = XGBRegressor()
model.load_model('heart_rate_model.model')

# Standardize features
scaler = StandardScaler()

# Exclude non-numeric columns before scaling
numeric_columns = test_data.select_dtypes(include=['float64', 'int64']).columns
test_data[numeric_columns] = scaler.fit_transform(test_data[numeric_columns])

# Predict on the test set
predictions = model.predict(test_data)

# Create a DataFrame with 'uuid' and predicted heart rates
result_df = pd.DataFrame({'uuid': uuid_column, 'Predicted_HR': predictions})

# Save the predictions to results.csv
result_df.to_csv('results.csv', index=False)


In [5]:
!cat results.csv

uuid,Predicted_HR
1ae30e0b-098e-46fc-a897-0a6661f26370,84.88413
428b41b3-9461-4c79-ab4e-d03b122b2553,90.85277
88f82ac7-02dd-447e-a289-22e8e22432c2,68.22056
1d09b18f-d82f-4c1a-bb2d-71fda6fea837,74.494804
a6302640-f70a-4a3a-ad36-a8c3d5df9400,71.14344
3f6508be-4b0a-4008-b701-49d8c2d5dd43,59.71483
a07d84c8-fc44-45ef-bb85-f06f06b70e9f,84.0379
f4a449db-a7ff-437b-852b-821a6e965f2f,68.14893
94364ef1-12e2-4ddd-9f35-99e270547849,60.131626
231d34f5-1028-4f2e-8e1d-00d086b0c218,78.70497


## Further enhancement: Hyperparameter tuning

In [ ]:
# Import necessary libraries
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from xgboost import XGBRegressor
from sklearn.metrics import mean_squared_error

# Load the training data
train_data = pd.read_csv('train_data.csv')

# Drop columns not needed for training (e.g., uuid, datasetId, condition)
train_data = train_data.drop(['uuid', 'datasetId', 'condition'], axis=1)

# Separate features and target variable
X = train_data.drop('HR', axis=1)
y = train_data['HR']

# Set a fixed value for the test size
test_size = 0.2

# Split the data into training and validation sets
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=test_size, random_state=42)

# Standardize features
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_valid_scaled = scaler.transform(X_valid)

# Define the hyperparameters to tune
params = {
    'max_depth': [3, 5, 7],
    'n_estimators': [100, 200, 300],
    'learning_rate': [0.01, 0.1, 0.2],
    'subsample': [0.5, 0.8, 1.0],
    'colsample_bytree': [0.5, 0.8, 1.0],
    'reg_lambda': [0.1, 1.0, 10.0]
}

# Initialize the XGBoost model with the gpu_hist tree method
model = XGBRegressor(tree_method='hist')

# Perform grid search to find the best parameters
from sklearn.model_selection import GridSearchCV
grid = GridSearchCV(model, params, scoring='neg_root_mean_squared_error', cv=5, verbose=1)
grid.fit(X_train_scaled, y_train, eval_set=[(X_valid_scaled, y_valid)], early_stopping_rounds=10)

# Print the best parameters and score
print(grid.best_params_)
print(grid.best_score_)

# Save the best model for later use
grid.best_estimator_.save_model('heart_rate_model.model')

# Load the test data
test_data = pd.read_csv(sys.argv[1])

# Drop columns not needed for prediction (e.g., datasetId, condition)
test_data = test_data.drop(['datasetId', 'condition'], axis=1)

# Extract the 'uuid' column for later inclusion in the results
uuid_column = test_data['uuid']

# Drop 'uuid' column as it's not needed for prediction
test_data = test_data.drop(['uuid'], axis=1)

# Load the trained model
model = XGBRegressor()
model.load_model('heart_rate_model.model')

# Standardize features
scaler = StandardScaler()

# Exclude non-numeric columns before scaling
numeric_columns = test_data.select_dtypes(include=['float64', 'int64']).columns
test_data[numeric_columns] = scaler.fit_transform(test_data[numeric_columns])

# Predict on the test set
predictions = model.predict(test_data)

# Create a DataFrame with 'uuid' and predicted heart rates
result_df = pd.DataFrame({'uuid': uuid_column, 'Predicted_HR': predictions})

# Save the predictions to results.csv
result_df.to_csv('results.csv', index=False)



Fitting 5 folds for each of 729 candidates, totalling 3645 fits
[0]	validation_0-rmse:10.30503
[1]	validation_0-rmse:10.20875
[2]	validation_0-rmse:10.13470
[3]	validation_0-rmse:10.03859
[4]	validation_0-rmse:9.94408
[5]	validation_0-rmse:9.85170
[6]	validation_0-rmse:9.78035
[7]	validation_0-rmse:9.68921
[8]	validation_0-rmse:9.59865
[9]	validation_0-rmse:9.50880
[10]	validation_0-rmse:9.41930
[11]	validation_0-rmse:9.33039
[12]	validation_0-rmse:9.24373
[13]	validation_0-rmse:9.15738
[14]	validation_0-rmse:9.07075
[15]	validation_0-rmse:8.98744
[16]	validation_0-rmse:8.90237
[17]	validation_0-rmse:8.81748
[18]	validation_0-rmse:8.73463
[19]	validation_0-rmse:8.65204
[20]	validation_0-rmse:8.56943
[21]	validation_0-rmse:8.49058
[22]	validation_0-rmse:8.43041
[23]	validation_0-rmse:8.36711
[24]	validation_0-rmse:8.28860
[25]	validation_0-rmse:8.21055
[26]	validation_0-rmse:8.15099
[27]	validation_0-rmse:8.07399
[28]	validation_0-rmse:7.99859
[29]	validation_0-rmse:7.92451


/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:889: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[30]	validation_0-rmse:7.85002
[31]	validation_0-rmse:7.77656
[32]	validation_0-rmse:7.70434
[33]	validation_0-rmse:7.63333
[34]	validation_0-rmse:7.56157
[35]	validation_0-rmse:7.49265
[36]	validation_0-rmse:7.43768
[37]	validation_0-rmse:7.38437
[38]	validation_0-rmse:7.31471
[39]	validation_0-rmse:7.24792
[40]	validation_0-rmse:7.18168
[41]	validation_0-rmse:7.11454
[42]	validation_0-rmse:7.06545
[43]	validation_0-rmse:7.01729
[44]	validation_0-rmse:6.95286
[45]	validation_0-rmse:6.90660
[46]	validation_0-rmse:6.85847
[47]	validation_0-rmse:6.79566
[48]	validation_0-rmse:6.73273
[49]	validation_0-rmse:6.66981
[50]	validation_0-rmse:6.62595
[51]	validation_0-rmse:6.56488
[52]	validation_0-rmse:6.50476
[53]	validation_0-rmse:6.44640
[54]	validation_0-rmse:6.38620
[55]	validation_0-rmse:6.32700
[56]	validation_0-rmse:6.26818
[57]	validation_0-rmse:6.20946
[58]	validation_0-rmse:6.16877
[59]	validation_0-rmse:6.11258
[60]	validation_0-rmse:6.05617
[61]	validation_0-rmse:6.00207
[62]	val

/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:889: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[29]	validation_0-rmse:7.92653
[30]	validation_0-rmse:7.85198
[31]	validation_0-rmse:7.77865
[32]	validation_0-rmse:7.70694
[33]	validation_0-rmse:7.63603
[34]	validation_0-rmse:7.56458
[35]	validation_0-rmse:7.49611
[36]	validation_0-rmse:7.44176
[37]	validation_0-rmse:7.38897
[38]	validation_0-rmse:7.31773
[39]	validation_0-rmse:7.25126
[40]	validation_0-rmse:7.18297
[41]	validation_0-rmse:7.11739
[42]	validation_0-rmse:7.06870
[43]	validation_0-rmse:7.01976
[44]	validation_0-rmse:6.95433
[45]	validation_0-rmse:6.90773
[46]	validation_0-rmse:6.86027
[47]	validation_0-rmse:6.79714
[48]	validation_0-rmse:6.73292
[49]	validation_0-rmse:6.66997
[50]	validation_0-rmse:6.62612
[51]	validation_0-rmse:6.56530
[52]	validation_0-rmse:6.50634
[53]	validation_0-rmse:6.44714
[54]	validation_0-rmse:6.38742
[55]	validation_0-rmse:6.32821
[56]	validation_0-rmse:6.26900
[57]	validation_0-rmse:6.21051
[58]	validation_0-rmse:6.17007
[59]	validation_0-rmse:6.11421
[60]	validation_0-rmse:6.05841
[61]	val

...

[14]	validation_0-rmse:3.00003
[15]	validation_0-rmse:2.79254
[16]	validation_0-rmse:2.59231
[17]	validation_0-rmse:2.41291
[18]	validation_0-rmse:2.24893
[19]	validation_0-rmse:2.10845
[20]	validation_0-rmse:1.97717
[21]	validation_0-rmse:1.86832
[22]	validation_0-rmse:1.78427
[23]	validation_0-rmse:1.71489
[24]	validation_0-rmse:1.62970
[25]	validation_0-rmse:1.55558
[26]	validation_0-rmse:1.50961
[27]	validation_0-rmse:1.44840
[28]	validation_0-rmse:1.39304
[29]	validation_0-rmse:1.33859
[30]	validation_0-rmse:1.29166
[31]	validation_0-rmse:1.25000
[32]	validation_0-rmse:1.21320
[33]	validation_0-rmse:1.18087
[34]	validation_0-rmse:1.15332
[35]	validation_0-rmse:1.12049
[36]	validation_0-rmse:1.09846
[37]	validation_0-rmse:1.07843
[38]	validation_0-rmse:1.05413
[39]	validation_0-rmse:1.03441
[40]	validation_0-rmse:1.01587
[41]	validation_0-rmse:1.00335
[42]	validation_0-rmse:0.98974
[43]	validation_0-rmse:0.97958
[44]	validation_0-rmse:0.96456
[45]	validation_0-rmse:0.95287
[46]	val

/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:889: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[16]	validation_0-rmse:2.53780
[17]	validation_0-rmse:2.35655
[18]	validation_0-rmse:2.19694
[19]	validation_0-rmse:2.06272
[20]	validation_0-rmse:1.93433
[21]	validation_0-rmse:1.82942
[22]	validation_0-rmse:1.74957
[23]	validation_0-rmse:1.68467
[24]	validation_0-rmse:1.60064
[25]	validation_0-rmse:1.52328
[26]	validation_0-rmse:1.47914
[27]	validation_0-rmse:1.41708
[28]	validation_0-rmse:1.35675
[29]	validation_0-rmse:1.30149
[30]	validation_0-rmse:1.25763
[31]	validation_0-rmse:1.21776
[32]	validation_0-rmse:1.18362
[33]	validation_0-rmse:1.15108
[34]	validation_0-rmse:1.12565
[35]	validation_0-rmse:1.09616
[36]	validation_0-rmse:1.07472
[37]	validation_0-rmse:1.05725
[38]	validation_0-rmse:1.03545
[39]	validation_0-rmse:1.01755
[40]	validation_0-rmse:1.00305
[41]	validation_0-rmse:0.99264
[42]	validation_0-rmse:0.98006
[43]	validation_0-rmse:0.96615
[44]	validation_0-rmse:0.95118
[45]	validation_0-rmse:0.93823
[46]	validation_0-rmse:0.92932
[47]	validation_0-rmse:0.91810
[48]	val

/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:889: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[23]	validation_0-rmse:1.66871
[24]	validation_0-rmse:1.58252
[25]	validation_0-rmse:1.51200
[26]	validation_0-rmse:1.46847
[27]	validation_0-rmse:1.40760
[28]	validation_0-rmse:1.35525
[29]	validation_0-rmse:1.30813
[30]	validation_0-rmse:1.26384
[31]	validation_0-rmse:1.22345
[32]	validation_0-rmse:1.18841
[33]	validation_0-rmse:1.15671
[34]	validation_0-rmse:1.12719
[35]	validation_0-rmse:1.09723
[36]	validation_0-rmse:1.07650
[37]	validation_0-rmse:1.06249
[38]	validation_0-rmse:1.04318
[39]	validation_0-rmse:1.02549
[40]	validation_0-rmse:1.01064
[41]	validation_0-rmse:0.99482
[42]	validation_0-rmse:0.98310
[43]	validation_0-rmse:0.97208
[44]	validation_0-rmse:0.96171
[45]	validation_0-rmse:0.95344
[46]	validation_0-rmse:0.94583
[47]	validation_0-rmse:0.93258
[48]	validation_0-rmse:0.92426
[49]	validation_0-rmse:0.91814
[50]	validation_0-rmse:0.91189
[51]	validation_0-rmse:0.90024
[52]	validation_0-rmse:0.89196
[53]	validation_0-rmse:0.88374
[54]	validation_0-rmse:0.87783
[55]	val